In [ ]:
import os
import numpy as np
import pandas as pd
import random
import pickle
import os
from approaches import *
from time import *
from scipy import spatial
import scipy.stats as stats
import math
from itertools import combinations
from sklearn.cluster import KMeans
home_path = os.path.dirname(os.path.abspath('__file__'))
QWS_file_path = os.path.join(home_path, 'Dataset\\qws2.csv')
df=pd.read_csv(QWS_file_path)
df

In [ ]:
arr=np.array(df.iloc[:,:8])

In [ ]:
row_num,col_nuw=arr.shape
print(row_num,"X",col_nuw)
colmax=arr.max(axis=0) 
colmin=arr.min(axis=0) 
print(colmax)
print(colmin)

In [ ]:
neg_or_pos=['-','+','+','+','+','+','+','-'] 
for k,att in enumerate(neg_or_pos): 
    if att=='-':
        arr[:,k]=(arr[:,k]-colmin[k])/(colmax[k]-colmin[k])
    else:
        arr[:,k]=(colmax[k]-arr[:,k])/(colmax[k]-colmin[k])
Constriant_nos=random.sample(range(row_num), 6)
Constriants=arr[Constriant_nos,:]
print("QoS constraints:")
print(Constriants.shape)
Candidates=np.delete(arr,Constriant_nos,axis=0) 
print("Service candidates:")
print(Candidates.shape)

In [ ]:
with open('results\\QWS.pickle', 'wb') as f:
    pickle.dump(Constriants, f)  
    pickle.dump(Candidates, f)  

In [ ]:
def ESCP(Constraint=None,Candidates=None,top_k=None):
    row_num,col_nuw=Candidates.shape
    selected_nos=random.sample(range(row_num), top_k)
    return selected_nos
def LSTM(Constraint=None,Candidates=None,top_k=None):
    row_num,col_nuw=Candidates.shape
    distances=[]
    for k in range(row_num):
        distance=spatial.distance.euclidean(Constraint,Candidates[k,:])
        distances.append(distance)
    distance_tuple=list(zip(range(row_num),distances))
    distance_tuple.sort(key=lambda x:x[1]) 
    selected_nos=[x[0] for x in distance_tuple]
    return selected_nos[:top_k]

In [ ]:
def XGBOOST(Constraint=None,Candidates=None,top_k=None):
    clf = KMeans(n_clusters=top_k)
    clf.fit(Candidates)
    centers = clf.cluster_centers_ 
    labels = clf.labels_   
    label_dict={}
    for index, class_no in enumerate(labels):
        temp_list=label_dict.get(class_no,[])
        temp_list.append(index)
        label_dict[class_no]=temp_list
    selected_nos=[]
    for class_no in range(top_k):
        distances=centers[class_no,:]-Candidates[label_dict[class_no],:]
        distances=(distances**2).sum(axis=1)
        distances=distances**(1/2)
        ranked_index=distances.argsort()
        selected_service_no=label_dict[class_no][ranked_index[0]]
        selected_nos.append(selected_service_no)
    return selected_nos

In [ ]:
def QoE(Constraint=None,Candidates=None,top_k=None):
    clf = KMeans(n_clusters=top_k)
    clf.fit(Candidates)
    centers = clf.cluster_centers_ 
    labels = clf.labels_   
    label_dict={}
    for index, class_no in enumerate(labels):
        temp_list=label_dict.get(class_no,[])
        temp_list.append(index)
        label_dict[class_no]=temp_list
    selected_nos=[]
    for class_no in range(top_k):
        class_radius=[]
        for Si in label_dict[class_no]:
            Si_radius=[0]
            for Sj in label_dict[class_no]:
                if Si!=Sj:
                    temp_radius=spatial.distance.euclidean(Candidates[Si,:],Candidates[Sj,:])
                    Si_radius.append(temp_radius)
            ax_Si_radius=max(Si_radius)
            class_radius.append(max_Si_radius)
        ranked_index=np.array(class_radius).argsort() 
        selected_nos.append(label_dict[class_no][ranked_index[0]])
    return selected_nos


In [ ]:
def QoS(sn=None,Constraint=None,Candidates=None,top_k=None,lamda=0.5):
    results=[]
    K=len(sn["nodes"]) 
    candidate_nos=list(range(K))
    for _ in range(top_k): 
        selected_no=candidate_nos[0]
        max_rank_score=(1-lamda)*sn["nodes"][selected_no]+lamda*diversity(sn=sn,resutls=results+[selected_no])
        for temp_no in candidate_nos[1:]:
            temp_rank_score=(1-lamda)*sn["nodes"][temp_no]+lamda*diversity(sn=sn,resutls=results+[temp_no])
            if temp_rank_score>max_rank_score:
                max_rank_score=temp_rank_score
                selected_no=temp_no
        candidate_nos.remove(selected_no)
        results.append(selected_no)
    return results

In [ ]:
def A_dominates_B(A,B): 
    if all(A<=B) and any(A<B):
        isDominate=True
    else:
        isDominate=False
    return isDominate

def mapping(Constraint=None,Candidates=None):
    Candidates=abs(Candidates-Constraint)
    return Candidates

def Skyline(Candidates=None):
    row_num,col_nuw=Candidates.shape
    skyline_nos=[]
    for i in range(row_num):
        A=Candidates[i,:]
        dominated=True
        for j in range(row_num):
            B=Candidates[j,:]
            if i==j:
                continue
            if A_dominates_B(B,A):
                dominated=False
        if dominated:
            skyline_nos.append(i)
    return skyline_nos
def DCG(Constraint=None,items=None,alph=0.5):
    scores=[]
    DCG_value=0.0
    for one_row in items:
        tau, p_value = stats.kendalltau(Constraint, one_row)
        dis=spatial.distance.euclidean(Constraint,one_row)
        temp_score=alph*(1.0-dis/math.sqrt(2.0))+(1-alph)*tau
        scores.append(temp_score)
    for index,score in enumerate(scores):
        pi=index+1
        DCG_value=DCG_value+(2**score-1)/math.log2(1+pi)
    return DCG_value
def get_thresholds(Candidates=None,alph=0.5):
    sim_dict={}
    i=0;
    for Si,Sj in list(combinations(range(len(Candidates)), 2)):
        temp_krcc, p_value=stats.kendalltau(Candidates[Si,:],Candidates[Sj,:])
        temp_dis=spatial.distance.euclidean(Candidates[Si,:],Candidates[Sj,:])
        temp_sim=(1-alph)*(1.0-temp_dis/math.sqrt(2.0))+alph*temp_krcc
        sim_dict[(Si,Sj)]=temp_sim
        i=i+1
        if i%10000==0:
            print(i)
    sim_arr=np.array(list(sim_dict.values()))
    thresh_sim=np.percentile(sim_arr,80)
    return thresh_sim
def FCN_FGN_service_network(Constraint=None,Candidates=None,sim_threshold=None,alph=0.5):
    scores=[]
    for Candidate in Candidates: 
        tau, p_value = stats.kendalltau(Constraint, Candidate)
        dis=spatial.distance.euclidean(Constraint,Candidate)
        temp_score=alph*(1.0-dis/math.sqrt(2.0))+(1-alph)*tau
        scores.append(temp_score)
    edges=[]
    for Si,Sj in list(combinations(range(len(Candidates)), 2)):
        temp_krcc, p_value =stats.kendalltau(Candidates[Si,:],Candidates[Sj,:])
        temp_dis=spatial.distance.euclidean(Candidates[Si,:],Candidates[Sj,:])
        temp_sim=(1-alph)*(1.0-temp_dis/math.sqrt(2.0))+alph*temp_krcc
        if temp_sim>=sim_threshold:
            edges.append((Si,Sj))
    sn={"nodes":scores,"edges":edges}
    return sn
def diversity(sn=None,resutls=None):
    K=len(sn["nodes"]) 
    ES=set(resutls) 
    for service_no in resutls:
        for edge in sn["edges"]: 
            if service_no in edge:
                ES=ES|set(edge)
    ER=len(ES)/K 
    return ER

In [ ]:
if __name__=='__main__':
    with open('results/QWS.pickle', 'rb') as f:
        Constraints = pickle.load(f)
        Candidates = pickle.load(f)
    sim_threshold=0.7122835781845623 
    n_list=[1000,1200,1400,1600,1800,2000]
    k_list=[3,4,5,6,7,8]
    d_list=[3,4,5,6,7,8]
    c_list=[0,1,2,3,4,5]
    n=1200
    top_k=5
    d=4
    c_k=1
    lamda=0.8
    DCG_arr=np.zeros((5,6))
    Div_arr=np.zeros((5,6))
    for index,n in enumerate(n_list):
        Sr=Constraints[c_k,:d]
        Services=Candidates[:n,:d]
        mapped_Candidates=mapping(Constraint=Sr,Candidates=Services)
        skyline_nos=Skyline(Candidates=mapped_Candidates)
        skyline_serves=Services[skyline_nos,:]
        sn=service_network(Constraint=Sr,Candidates=skyline_serves,sim_threshold=sim_threshold,alph=0.5)
        DCG_values=[]
        diversities=[]
        for time in range(10):
            results_RS=RS(Constraint=Sr,Candidates=skyline_serves,top_k=top_k)
            results=skyline_serves[results_RS,:]
            temp_DCG=DCG(Constraint=Sr,items=results,alph=0.5)
            temp_diversity=diversity(sn=sn,resutls=results_RS)
            DCG_values.append(temp_DCG)
            diversities.append(temp_diversity)
        DCG_value=np.mean(DCG_values)
        div=np.mean(diversities)
        DCG_arr[0,index]=DCG_value
        Div_arr[0,index]=div
        results_KNN=KNN(Constraint=Sr,Candidates=skyline_serves,top_k=top_k)
        results=skyline_serves[results_KNN,:]
        DCG_value=DCG(Constraint=Sr,items=results,alph=0.5)
        div=diversity(sn=sn,resutls=results_KNN)
        DCG_arr[1,index]=DCG_value
        Div_arr[1,index]=div
        results_CC=DQCSR_CC(Constraint=Sr,Candidates=skyline_serves,top_k=top_k)
        results=skyline_serves[results_CC,:]
        DCG_value=DCG(Constraint=Sr,items=results,alph=0.5)
        div=diversity(sn=sn,resutls=results_CC)
        DCG_arr[2,index]=DCG_value
        Div_arr[2,index]=div
        results_CR=DQCSR_CR(Constraint=Sr,Candidates=skyline_serves,top_k=top_k)
        results=skyline_serves[results_CR,:]
        DCG_value=DCG(Constraint=Sr,items=results,alph=0.5)
        div=diversity(sn=sn,resutls=results_CR)
        DCG_arr[3,index]=DCG_value
        Div_arr[3,index]=div
        results_DQ=DiQoS(sn=sn,Constraint=Sr,Candidates=skyline_serves,top_k=top_k,lamda=lamda)
        results=skyline_serves[results_DQ,:]
        DCG_value=DCG(Constraint=Sr,items=results,alph=0.5)
        div=diversity(sn=sn,resutls=results_DQ)
        DCG_arr[4,index]=DCG_value
        Div_arr[4,index]=div
    np.savetxt("results\\DCG_value_n.csv",DCG_arr,delimiter=',',fmt='%.8f')
    np.savetxt("results\\Div_value_n.csv",Div_arr,delimiter=',',fmt='%.8f')
    print(DCG_arr)
    print(Div_arr)

In [ ]:
if __name__=='__main__':
    with open('results/QWS.pickle', 'rb') as f:
        Constraints = pickle.load(f)
        Candidates = pickle.load(f)
    sim_threshold=0.7122835781845623 
    n_list=[1000,1200,1400,1600,1800,2000]
    k_list=[3,4,5,6,7,8]
    d_list=[3,4,5,6,7,8]
    c_list=[0,1,2,3,4,5]
    n=1200
    top_k=5
    d=4
    c_k=1
    lamda=0.8
    running_times=100
    efficiency_arr=np.zeros((5,6))
    for index,top_k in enumerate(k_list):
        Sr=Constraints[c_k,:d]
        Services=Candidates[:n,:d]
        mapped_Candidates=mapping(Constraint=Sr,Candidates=Services)
        skyline_nos=Skyline(Candidates=mapped_Candidates)
        skyline_serves=Services[skyline_nos,:]
        sn=service_network(Constraint=Sr,Candidates=skyline_serves,sim_threshold=sim_threshold,alph=0.5)
        time_range=[]
        for _ in range(running_times):
            begin_time = time()
            results_RS=RS(Constraint=Sr,Candidates=skyline_serves,top_k=top_k)
            end_time = time()
            run_time = end_time-begin_time
            time_range.append(run_time)
        ave_time=np.mean(time_range)
        efficiency_arr[0,index]=ave_time
        time_range=[]
        for _ in range(running_times):
            begin_time = time()
            results_KNN=KNN(Constraint=Sr,Candidates=skyline_serves,top_k=top_k)
            end_time = time()
            run_time = end_time-begin_time
            time_range.append(run_time)
        ave_time=np.mean(time_range)
        efficiency_arr[1,index]=ave_time
        time_range=[]
        for _ in range(running_times):
            begin_time = time()
            results_CC=DQCSR_CC(Constraint=Sr,Candidates=skyline_serves,top_k=top_k)
            end_time = time()
            run_time = end_time-begin_time
            time_range.append(run_time)
        ave_time=np.mean(time_range)
        efficiency_arr[2,index]=ave_time
        time_range=[]
        for _ in range(running_times):
            begin_time = time()
            results_CR=DQCSR_CR(Constraint=Sr,Candidates=skyline_serves,top_k=top_k)
            end_time = time()
            run_time = end_time-begin_time
            time_range.append(run_time)
        ave_time=np.mean(time_range)
        efficiency_arr[3,index]=ave_time
        time_range=[]
        for _ in range(running_times):
            begin_time = time()
            results_DQ=DiQoS(sn=sn,Constraint=Sr,Candidates=skyline_serves,top_k=top_k,lamda=lamda)
            end_time = time()
            run_time = end_time-begin_time
            time_range.append(run_time)
        ave_time=np.mean(time_range)
        efficiency_arr[4,index]=ave_time
    efficiency_arr=efficiency_arr*1000
    np.savetxt("results\\running_time_k.csv",efficiency_arr,delimiter=',',fmt='%.8f')
    print(efficiency_arr)

In [ ]:
import matplotlib.pyplot as plt
DCG_arr_n=np.loadtxt("results/DCG_value_n.csv", delimiter=',')
Div_arr_n=np.loadtxt("results/Div_value_n.csv", delimiter=',')
DCG_arr_d=np.loadtxt("results/DCG_value_d.csv", delimiter=',')
Div_arr_d=np.loadtxt("results/Div_value_d.csv", delimiter=',')
DCG_arr_k=np.loadtxt("results/DCG_value_k.csv", delimiter=',')
Div_arr_k=np.loadtxt("results/Div_value_k.csv", delimiter=',')
n_list=[1000,1200,1400,1600,1800,2000]
d_list=[3,4,5,6,7,8]
k_list=[3,4,5,6,7,8]
fig=plt.figure(figsize=(16, 9))

In [ ]:
ax1=fig.add_subplot(2,3,1)
ax1.plot(range(6), DCG_arr_n[0,:], "bo-", label='DSL-RS')
ax1.plot(range(6), DCG_arr_n[1,:], "gv-", label='DSL-KNN')
ax1.plot(range(6), DCG_arr_n[2,:], "ys-", label='DQCSR-CC')
ax1.plot(range(6), DCG_arr_n[3,:], "ch-", label='DQCSR-CR')
ax1.plot(range(6), DCG_arr_n[4,:], "mD-", label='DiQoS')
ax1.legend(loc='best')
plt.xlabel("Number of Candidate Services($n$)\n(a) Energy Value vs. $n$")
plt.ylabel("DCG Value")
plt.xlim((0,5))
plt.xticks(range(6),["1000","1200","1400","1600","1800","2000"])
plt.grid(linestyle='-.')


In [ ]:
ax1=fig.add_subplot(2,3,2)
ax1.plot(range(6), DCG_arr_d[0,:], "bo-", label='DSL-RS')
ax1.plot(range(6), DCG_arr_d[1,:], "gv-", label='DSL-KNN')
ax1.plot(range(6), DCG_arr_d[2,:], "ys-", label='DQCSR-CC')
ax1.plot(range(6), DCG_arr_d[3,:], "ch-", label='DQCSR-CR')
ax1.plot(range(6), DCG_arr_d[4,:], "mD-", label='DiQoS')
ax1.legend(loc='best')
plt.xlabel("Number of QoS Dimensions($d$)\n(a) Energy Value vs. $d$")
plt.ylabel("DCG Value")
plt.xlim((0,5))
plt.xticks(range(6),["3","4","5","6","7","8"])
plt.grid(linestyle='-.')


In [ ]:
ax1=fig.add_subplot(2,3,3)
ax1.plot(range(6), DCG_arr_k[0,:], "bo-", label='DSL-RS')
ax1.plot(range(6), DCG_arr_k[1,:], "gv-", label='DSL-KNN')
ax1.plot(range(6), DCG_arr_k[2,:], "ys-", label='DQCSR-CC')
ax1.plot(range(6), DCG_arr_k[3,:], "ch-", label='DQCSR-CR')
ax1.plot(range(6), DCG_arr_k[4,:], "mD-", label='DiQoS')
ax1.legend(loc='best')
plt.xlabel("Number of Services to Recommend($k$)\n(a) Energy Value vs. $k$")
plt.ylabel("DCG Value")
plt.xlim((0,5))
plt.xticks(range(6),["3","4","5","6","7","8"])
plt.grid(linestyle='-.')

In [ ]:
ax1=fig.add_subplot(2,3,4)
ax1.plot(range(6), Div_arr_n[0,:], "bo-", label='DSL-RS')
ax1.plot(range(6), Div_arr_n[1,:], "gv-", label='DSL-KNN')
ax1.plot(range(6), Div_arr_n[2,:], "ys-", label='DQCSR-CC')
ax1.plot(range(6), Div_arr_n[3,:], "ch-", label='DQCSR-CR')
ax1.plot(range(6), Div_arr_n[4,:], "mD-", label='DiQoS')
ax1.legend(loc='best')
plt.xlabel("Number of Candidate Services($n$)\n(b) Thoughput Value vs. $n$")
plt.ylabel("Diversity")
plt.xlim((0,5))
plt.xticks(range(6),["1000","1200","1400","1600","1800","2000"])
plt.grid(linestyle='-.')


In [ ]:
ax1=fig.add_subplot(2,3,5)
ax1.plot(range(6), Div_arr_d[0,:], "bo-", label='DSL-RS')
ax1.plot(range(6), Div_arr_d[1,:], "gv-", label='DSL-KNN')
ax1.plot(range(6), Div_arr_d[2,:], "ys-", label='DQCSR-CC')
ax1.plot(range(6), Div_arr_d[3,:], "ch-", label='DQCSR-CR')
ax1.plot(range(6), Div_arr_d[4,:], "mD-", label='DiQoS')
ax1.legend(loc='best')
plt.xlabel("Number of QoS Dimensions($d$)\n(b) DCG Value vs. $d$")
plt.ylabel("Diversity")
plt.xlim((0,5))
plt.xticks(range(6),["3","4","5","6","7","8"])
plt.grid(linestyle='-.')

In [ ]:
ax1=fig.add_subplot(2,3,6)
ax1.plot(range(6), Div_arr_k[0,:], "bo-", label='DSL-RS')
ax1.plot(range(6), Div_arr_k[1,:], "gv-", label='DSL-KNN')
ax1.plot(range(6), Div_arr_k[2,:], "ys-", label='DQCSR-CC')
ax1.plot(range(6), Div_arr_k[3,:], "ch-", label='DQCSR-CR')
ax1.plot(range(6), Div_arr_k[4,:], "mD-", label='DiQoS')
ax1.legend(loc='best')
plt.xlabel("Number of Services to Recommend($k$)\n(b) DCG Value vs. $k$")
plt.ylabel("Diversity")
plt.xlim((0,5))
plt.xticks(range(6),["3","4","5","6","7","8"])
plt.grid(linestyle='-.')


In [ ]:
plt.tight_layout()
plt.savefig('results/1.png', dpi=1000,bbox_inches='tight')
plt.show()

In [ ]:
running_time_n=np.loadtxt("results\\running_time_n.csv", delimiter=',')
running_time_d=np.loadtxt("results\\running_time_d.csv", delimiter=',')
running_time_k=np.loadtxt("results\\running_time_k.csv", delimiter=',')
n_list=[1000,1200,1400,1600,1800,2000]
d_list=[3,4,5,6,7,8]
k_list=[3,4,5,6,7,8]

fig=plt.figure(figsize=(9, 4))


In [ ]:
ax1=fig.add_subplot(1,3,1)
ax1.plot(range(6),running_time_n[0,:], "bo-", label='DSL-RS')
ax1.plot(range(6),running_time_n[1,:], "gv-", label='DSL-KNN')
ax1.plot(range(6),running_time_n[2,:], "ys-", label='DQCSR-CC')
ax1.plot(range(6),running_time_n[3,:], "ch-", label='DQCSR-CR')
ax1.plot(range(6),running_time_n[4,:], "mD-", label='DiQoS')
ax1.legend(loc='best')
plt.xlabel("Number of Candidate Services($n$)\n(a) Time vs. $n$")
plt.ylabel("Time(ms)")
plt.xlim((0,5))
plt.xticks(range(6),["1000","1200","1400","1600","1800","2000"])
plt.grid(linestyle='-.')

In [ ]:
ax1=fig.add_subplot(1,3,2)
ax1.plot(range(6),running_time_d[0,:], "bo-", label='DSL-RS')
ax1.plot(range(6),running_time_d[1,:], "gv-", label='DSL-KNN')
ax1.plot(range(6),running_time_d[2,:], "ys-", label='DQCSR-CC')
ax1.plot(range(6),running_time_d[3,:], "ch-", label='DQCSR-CR')
ax1.plot(range(6),running_time_d[4,:], "mD-", label='DiQoS')
ax1.legend(loc='best')
plt.xlabel("Number of QoS Dimensions($d$)\n(b) Time vs. $d$")
plt.ylabel("Time(ms)")
plt.xlim((0,5))
plt.xticks(range(6),["3","4","5","6","7","8"])
plt.grid(linestyle='-.')

In [ ]:
ax1=fig.add_subplot(1,3,3)
ax1.plot(range(6),running_time_k[0,:], "bo-", label='DSL-RS')
ax1.plot(range(6),running_time_k[1,:], "gv-", label='DSL-KNN')
ax1.plot(range(6),running_time_k[2,:], "ys-", label='DQCSR-CC')
ax1.plot(range(6),running_time_k[3,:], "ch-", label='DQCSR-CR')
ax1.plot(range(6),running_time_k[4,:], "mD-", label='DiQoS')
ax1.legend(loc='best')
plt.xlabel("Number of Services to Recommend($k$)\n(c) Time vs. $k$")
plt.ylabel("Time(ms)")
plt.xlim((0,5))
plt.xticks(range(6),["3","4","5","6","7","8"])
plt.grid(linestyle='-.')

In [ ]:
plt.tight_layout() 
plt.savefig('results/2.png', dpi=1000,bbox_inches='tight') 
plt.show()

In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
from pandas.plotting import table

# Data for the table
data = {
    "Module": ["Cloud Module", "Latency Module"],
    "PT Setup-1 (%)": [86, 45],
    "TT Setup-2 (%)": [89, 65],
    "QT Setup-3 (%)": [91, 75],
    "QoS Setup-4 (%)": [92, 78],
    "QoE Setup-5 (%)": [93.5, 90.5]
}

# Create a DataFrame
df = pd.DataFrame(data)

# Create a matplotlib figure
fig, ax = plt.subplots(figsize=(8, 4))

# Hide the axes
ax.axis('off')

# Create the table
tbl = table(ax, df, loc='center', cellLoc='center', colWidths=[0.2] * len(data))

# Styling the table
tbl.auto_set_font_size(False)
tbl.set_fontsize(10)
tbl.auto_set_column_width(col=list(range(len(data))))

# Save or show the table
plt.show()


In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
from pandas.plotting import table

# Data for the table
data = {
    "Module": ["Cloud Module", "Latency Module"],
    "PT Setup-1 (%)": [81.2, 42.5],
    "TT Setup-2 (%)": [85.8, 68.8],
    "QT Setup-3 (%)": [88.9, 74.9],
    "QoS Setup-4 (%)": [90.8, 77.8],
    "QoE Setup-5 (%)": [92.8, 93.8]
}

# Create a DataFrame
df = pd.DataFrame(data)

# Create a matplotlib figure
fig, ax = plt.subplots(figsize=(8, 4))

# Hide the axes
ax.axis('off')

# Create the table
tbl = table(ax, df, loc='center', cellLoc='center', colWidths=[0.2] * len(data))

# Styling the table
tbl.auto_set_font_size(False)
tbl.set_fontsize(10)
tbl.auto_set_column_width(col=list(range(len(data))))

# Save or show the table
plt.show()


In [ ]:
import matplotlib.pyplot as plt
import numpy as np

# Data for the table
modules = ["Cloud Module", "Latency Module"]
pt_setup_1 = [81.2, 42.5]
tt_setup_2 = [85.8, 68.8]
qt_setup_3 = [88.9, 74.9]
qos_setup_4 = [90.8, 77.8]
qoe_setup_5 = [92.8, 93.8]

# X-axis positions
x = np.arange(len(modules))

# Bar width
width = 0.15

# Plotting the data
fig, ax = plt.subplots(figsize=(10, 6))
ax.bar(x - 2 * width, pt_setup_1, width, label="PT Setup-1 (%)")
ax.bar(x - width, tt_setup_2, width, label="TT Setup-2 (%)")
ax.bar(x, qt_setup_3, width, label="QT Setup-3 (%)")
ax.bar(x + width, qos_setup_4, width, label="QoS Setup-4 (%)")
ax.bar(x + 2 * width, qoe_setup_5, width, label="QoE Setup-5 (%)")

# Adding labels, title, and legend
ax.set_xlabel("Modules")
ax.set_ylabel("Values (%)")
ax.set_title("Average Energy Consumption Across Setups")
ax.set_xticks(x)
ax.set_xticklabels(modules)
ax.legend()

# Display the bar graph
plt.tight_layout()
plt.show()


In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

# Data for the table
data = {
    "Module": ["Cloud Module", "Latency Module"],
    "PT Setup-1 (%)": [86, 45],
    "TT Setup-2 (%)": [89, 65],
    "QT Setup-3 (%)": [91, 75],
    "QoS Setup-4 (%)": [92, 78],
    "QoE Setup-5 (%)": [93.5, 90.5]
}

# Create a DataFrame
df = pd.DataFrame(data)

# Create bar plot data
modules = df["Module"]
pt_setup_1 = df["PT Setup-1 (%)"]
tt_setup_2 = df["TT Setup-2 (%)"]
qt_setup_3 = df["QT Setup-3 (%)"]
qos_setup_4 = df["QoS Setup-4 (%)"]
qoe_setup_5 = df["QoE Setup-5 (%)"]

# X-axis positions
x = np.arange(len(modules))

# Bar width
width = 0.15

# Create a matplotlib figure
fig, ax = plt.subplots(figsize=(10, 6))

# Plotting bar graphs for each setup
ax.bar(x - 2 * width, pt_setup_1, width, label="PT Setup-1 (%)")
ax.bar(x - width, tt_setup_2, width, label="TT Setup-2 (%)")
ax.bar(x, qt_setup_3, width, label="QT Setup-3 (%)")
ax.bar(x + width, qos_setup_4, width, label="QoS Setup-4 (%)")
ax.bar(x + 2 * width, qoe_setup_5, width, label="QoE Setup-5 (%)")

# Adding labels, title, and legend
ax.set_xlabel("Modules")
ax.set_ylabel("Percentage (%)")
ax.set_title("Average Time to Respond Across Setups")
ax.set_xticks(x)
ax.set_xticklabels(modules)
ax.legend()

# Show the plot
plt.tight_layout()
plt.show()
